In [2]:
from google.colab import files
uploaded= files.upload()

Saving database.sqlite.zip to database.sqlite.zip


In [3]:
pip install catboost scikit-learn scipy

In [9]:
import pandas as pd
import sqlite3
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from catboost import CatBoostClassifier, Pool

# ✅ Load Kaggle dataset from SQLite
# Unzip the database file
import zipfile
with zipfile.ZipFile("database.sqlite.zip", 'r') as zip_ref:
    zip_ref.extractall(".")

# Connect to the database
con = sqlite3.connect("database.sqlite")

# Read data from the database into a pandas DataFrame
df = pd.read_sql_query("SELECT * FROM Reviews", con)

# Close the connection
con.close()

print(df[['Text', 'Score']].head())

# 🧹 Simple preprocessing: keep reviews with Score 1 or 5 (binary classification)
df = df[df['Score'].isin([1, 5])]
df = df.dropna(subset=['Text'])

X_text = df['Text']
y = (df['Score'] == 5).astype(int)  # 1 if positive review

                                                Text  Score
0  I have bought several of the Vitality canned d...      5
1  Product arrived labeled as Jumbo Salted Peanut...      1
2  This is a confection that has been around a fe...      4
3  If you are looking for the secret ingredient i...      2
4  Great taffy at a great price.  There was a wid...      5


In [10]:
vectorizer = TfidfVectorizer(max_features=5000)
X_sparse = vectorizer.fit_transform(X_text)

print(f"Sparse Shape: {X_sparse.shape}")
print(f"Sparsity: {100 * (1.0 - X_sparse.count_nonzero() / (X_sparse.shape[0] * X_sparse.shape[1])):.2f}%")

Sparse Shape: (415390, 5000)
Sparsity: 99.02%


In [11]:
# 🧪 Train-test split
X_train, X_test, y_train, y_test = train_test_split(
    X_sparse, y, test_size=0.2, random_state=42, stratify=y
)


In [12]:
# 🐈‍⬛ CatBoost with sparse input
train_pool = Pool(X_train, y_train)
test_pool = Pool(X_test, y_test)

model = CatBoostClassifier(iterations=100, learning_rate=0.1, depth=6, verbose=10)
model.fit(train_pool, eval_set=test_pool)


0:	learn: 0.6102887	test: 0.6106654	best: 0.6106654 (0)	total: 6.86s	remaining: 11m 19s
10:	learn: 0.3311281	test: 0.3319815	best: 0.3319815 (10)	total: 38.7s	remaining: 5m 12s
20:	learn: 0.2891627	test: 0.2900957	best: 0.2900957 (20)	total: 1m 9s	remaining: 4m 23s
30:	learn: 0.2678970	test: 0.2691431	best: 0.2691431 (30)	total: 1m 43s	remaining: 3m 49s
40:	learn: 0.2541265	test: 0.2555340	best: 0.2555340 (40)	total: 2m 14s	remaining: 3m 14s
50:	learn: 0.2440084	test: 0.2454868	best: 0.2454868 (50)	total: 2m 47s	remaining: 2m 41s
60:	learn: 0.2348150	test: 0.2365393	best: 0.2365393 (60)	total: 3m 22s	remaining: 2m 9s
70:	learn: 0.2272156	test: 0.2288877	best: 0.2288877 (70)	total: 3m 59s	remaining: 1m 38s
80:	learn: 0.2212816	test: 0.2228732	best: 0.2228732 (80)	total: 4m 29s	remaining: 1m 3s
90:	learn: 0.2154575	test: 0.2171494	best: 0.2171494 (90)	total: 5m 2s	remaining: 29.9s
99:	learn: 0.2108008	test: 0.2124823	best: 0.2124823 (99)	total: 5m 29s	remaining: 0us

bestTest = 0.2124823

In [13]:
accuracy = model.score(test_pool)
print(f"Accuracy: {accuracy:.4f}")

Accuracy: 0.9178
